In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import requests # requests for the report website
import json
from sec_edgar_api import EdgarClient
from bs4 import BeautifulSoup # Import BeautifulSoup
import re # import re module for REGEXes
import time
import os
import html2text

import nltk
from nltk.tokenize import sent_tokenize
nltk.download('punkt')

import yfinance as yf

# Create a folder for save data
# os.mkdir('Data') 

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\lenovo\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [3]:
# read bloomberg excel with company
df = pd.read_excel('C:/Users/lenovo/Desktop/UCL/Final dissertation/code/Industrial product G.xlsx')
df = df[1:]
df['Unnamed: 1'] = df['Unnamed: 1'].str.replace(r' \b\w{2} Equity\b', '', regex=True)
display(df['Unnamed: 1'])

1      SCWO
2       MMM
3       AOS
4      AAON
5       AIR
       ... 
254    XMTR
255     XYL
256     ZWS
257    LASR
258     NVT
Name: Unnamed: 1, Length: 258, dtype: object

In [4]:
# AAPL https://www.sec.gov/Archives/edgar/data/320193/000032019323000106/0000320193-23-000106.txt
# Google https://www.sec.gov/Archives/edgar/data/1652044/000165204424000022/0001652044-24-000022.txt

r = requests.get('https://www.sec.gov/Archives/edgar/data/320193/000032019323000106/0000320193-23-000106.txt',
                headers={'User-Agent':"test@gmail.com"})
raw_10k = r.text
#print(raw_10k)
text=html2text.html2text(raw_10k)
# f = open(f"AAPL2024test.txt","x+")
# f.write(text)
# f.close


In [5]:
def SearchIndexContents(text):
    IndexContent = re.compile(r'((ITEM \d+\.\ *\s*(.*?)\n))|(Item \d+\.\ *\s*(.*?)\n)').finditer(text)

    ItemIndex_df = pd.DataFrame([(match.group().strip(), match.start(), match.end()) for match in IndexContent])
    ItemIndex_df.columns = ['Item', 'start', 'end']
    if len(ItemIndex_df) > 16:
        ItemIndex_df = ItemIndex_df[(len(ItemIndex_df)-16):len(ItemIndex_df)]
    ItemIndex_df = ItemIndex_df.reset_index(drop=True)
    display(ItemIndex_df)
    return ItemIndex_df

#ReportIndex = SearchIndexContents(text)
#display(ReportIndex)

In [6]:
CompanyTickers = requests.get('https://www.sec.gov/files/company_tickers.json',
                              headers={'User-Agent':"test@gmail.com"})

CompanyTicker = open('CompanyTickers.json','w+')
CompanyTicker.write(json.dumps(CompanyTickers.json()))
CompanyTicker.close()

CompanyData = pd.DataFrame.from_dict(CompanyTickers.json(), orient='index')
display(CompanyData)

cik_str ticker                   title
0       320193   AAPL              Apple Inc.
1       789019   MSFT          MICROSOFT CORP
2      1045810   NVDA             NVIDIA CORP
3      1652044  GOOGL           Alphabet Inc.
4      1018724   AMZN          AMAZON COM INC
...        ...    ...                     ...
10225   927971   SHNY  BANK OF MONTREAL /CAN/
10226   927971   GDXU  BANK OF MONTREAL /CAN/
10227   927971   NRGD  BANK OF MONTREAL /CAN/
10228   927971   NRGU  BANK OF MONTREAL /CAN/
10229   927971   OILD  BANK OF MONTREAL /CAN/

[10230 rows x 3 columns]

In [7]:
def FindCompanyCik(Ticker):
    for i in CompanyTickers.json().keys():
        if CompanyTickers.json()[i]['ticker'] ==Ticker:
            print(CompanyTickers.json()[i])   # can be not show
            return CompanyTickers.json()[i]['cik_str']
            break
# CompanyName = 'GOOGL'
# Companycik = FindCompanyCik(CompanyName)

In [8]:
def Extractedtext(dataframe:pd,Item:int,report:str):
    # Locate the start of 'Item-1'
    start_index = dataframe['start'][Item-1]

    # Locate the start of 'Item'
    end_index = dataframe['start'][Item]
    
    # Check if both items were found
    if start_index != -1 and end_index != -1:
        # Extract the text between 'Item 1' and 'Item 2'
        # Adjust indices according to your needs if you want to include or exclude the labels themselves
        extracted_text = report[start_index:end_index].strip()
        extracted_text = re.sub(r'\*|\_|\||\#|\-', '', extracted_text)
        extracted_text = re.sub(r'\n', ' ', extracted_text)

    else:
        print(f"{dataframe} in Item {Item} markers not found in text.") 
        extracted_text = None
    return(extracted_text)

# Extracted_text = Extractedtext(ReportIndex,1,text)
# print(Extracted_text)

In [10]:
def ExtractESG(text):
    ReportIndex = SearchIndexContents(text)

    item1 = Extractedtext(ReportIndex,1,text)
    item3 = Extractedtext(ReportIndex,3,text)
    item7 = Extractedtext(ReportIndex,7,text)
    item10 = Extractedtext(ReportIndex,10,text)
    item11 = Extractedtext(ReportIndex,11,text)
    item12 = Extractedtext(ReportIndex,12,text)
    All = item1 + ' '+ item3 +' '+ item7 +' '+ item10 +' '+ item11 +' '+ item12
    Split = sent_tokenize(All)
    
    return Split

# split = ExtractESG(text)
# print(split)

# # Create a folder for save data
# # os.mkdir('ReportSplitSentences') 
# df = pd.DataFrame(split)
# # df.columns = ['Sentences']

# df.to_csv('C:\Users\lenovo\Desktop\UCL\Final dissertation\code\Data',index=False)

# display(split)

In [11]:
def checkExistingof10k (Companycik):
    edgar = EdgarClient(user_agent="test@gmail.com")
    try:
        test = edgar.get_company_concept(cik=Companycik, taxonomy="us-gaap", tag="AccountsPayableCurrent")
        print(test)    #can be not show
        reportRecord = pd.DataFrame.from_dict(test['units']['USD'])
        pass
    except:
        return False
        pass
    # display(reportRecord)
    type='10-K'
    if type in reportRecord['form'].values:
        return True
    else:
        return False 

In [10]:
# counting company quantity in stock

#time consuming
# count = 0
# industry = []
# for name in df['Unnamed: 1']:
#     if name in CompanyData['ticker'].values:
#         if checkExistingof10k(FindCompanyCik(name)):
#             count = count + 1
#             print(count)
#             industry.append(name)    
#             print(industry) 

In [12]:
IndustrialProduct = ['MMM', 'AAON', 'AIR', 'AGCO', 'AME', 'POWW', 'AZZ', 'AYI', 'AEIS', 'AVAV', 'ALG', 'AIN', 'ALLE', 'ALNT', 'ALSN', 'AMSC', 'AP', 'APH', 'AGX', 'ARQ', 'ARTW', 'ACNT', 'ASTE', 'ATRO', 'ATKR', 'AXON', 'BWXT', 'BW', 'BMI', 'B', 'BELFA', 'BDC', 'BLNK', 'BE', 'BLBD', 'BA', 'BC', 'CVU', 'CSWI', 'CVV', 'WHD', 'CDRE', 'CWH', 'CARR', 'CAT', 'CHPT', 'GTLS', 'CGNX', 'CVGI', 'CIX', 'CMT', 'CMI', 'CW', 'DCI', 'PLOW', 'DOV', 'DCO', 'ENG', 'ESE', 'EML', 'ETN', 'EMR', 'WATT', 'ERII', 'EPAC', 'ENOV', 'NPO', 'ESP', 'FARO', 'FSS', 'FLS', 'FELE', 'RAIL', 'FTEK', 'GENC', 'GNRC', 'GD', 'GE', 'ROCK', 'GRC', 'GGG', 'EAF', 'GHM', 'HEI', 'HAYW', 'HLIO', 'HXL', 'HI', 'HON', 'HWM', 'HUBB', 'HII', 'HURC', 'HYFM', 'HY', 'ITT', 'ICHR', 'ITW', 'IR', 'ISSC', 'IIIN', 'IVAC', 'ITRI', 'JBT', 'JCI', 'JOUT', 'KAI', 'KMT', 'KEYS', 'KE', 'KTOS', 'FSTR', 'LHX', 'LYTS', 'LII', 'LECO', 'LNN', 'LQMT', 'LFUS', 'LMT', 'LXFR', 'MSA', 'MBUU', 'MPX', 'MCFT', 'MEC', 'MRCY', 'MLAB', 'MIDD', 'MOD', 'MLI', 'MWA', 'NL', 'NNBR', 'NSSC', 'NPK', 'NKLA', 'NDSN', 'NOC', 'NOVT', 'OSIS', 'ZEUS', 'OFLX', 'OESX', 'OSK', 'OTIS', 'PH', 'PNR', 'PII', 'POWL', 'PSIX', 'PRLB', 'QSEP', 'RBC', 'REVG', 'RFIL', 'RTX', 'RRX', 'RS', 'REFR', 'ROK', 'RYI', 'SIF', 'SPXC', 'ST', 'SHYF', 'SMRT', 'SNA', 'SPR', 'SXI', 'SWK', 'SRI', 'STRT', 'SYM', 'SYPR', 'TEL', 'TAYD', 'TNC', 'TEX', 'THR', 'THO', 'TKR', 'TWI', 'TTC', 'TT', 'TDG', 'TG', 'TRMB', 'TGI', 'TSPH', 'TWIN', 'VMI', 'VRT', 'WNC', 'WTS', 'WAB', 'WYY', 'WGO', 'WWD', 'WKHS', 'WOR', 'WRAP', 'XMTR', 'XYL', 'ZWS', 'LASR', 'NVT']

In [17]:
# Finding the index of 'WHD'
index = IndustrialProduct.index('WHD')

# Slicing the list from 'WHD' onwards
filtered_list = IndustrialProduct[index:]

# Printing the filtered list
len(filtered_list)

167

In [14]:
def Download10kdata(companyCik,CompanyName,CompanyRec):
    edgar = EdgarClient(user_agent="test@gmail.com")
    test = edgar.get_company_concept(cik=companyCik, taxonomy="us-gaap", tag="AccountsPayableCurrent")
    reportRecord = pd.DataFrame.from_dict(test['units']['USD'])
    Company10K = reportRecord[reportRecord['form']=='10-K']
    Company10K=Company10K.drop_duplicates(['fy'])
    Company10K=Company10K.set_index('fy')
    for i,row in Company10K.iterrows():  
        accn = row['accn']
        print(f'{CompanyName}-{accn}')
        accnid = accn.replace('-','')
        #print(accnid)
        #time.sleep(1)
        try:
            Report_10K = requests.get(f'https://www.sec.gov/Archives/edgar/data/{companyCik}/{accnid}/{accn}.txt',
                              headers={'User-Agent':"test@gmail.com"})
            #print(Report_10K)
            raw_10k = Report_10K.text
            clear10K = html2text.html2text(raw_10k)
            #print(clear10K)
            split = ExtractESG(clear10K)
            #print(split)
            # Create a folder for save data
            df = pd.DataFrame(split)
            df.to_csv(f"C:/Users/lenovo/Desktop/UCL/Final dissertation/code/Data/{CompanyName}-{i}.csv", index=False)
            CompanyRec.loc[len(CompanyRec.index)]=[CompanyName,i,companyCik, accn,'True',len(df.index)]
            pass
        except:
            CompanyRec.loc[len(CompanyRec.index)]=[CompanyName,i,companyCik, accn,'False',0]
            pass

In [15]:
downloadRec = pd.DataFrame(columns=['CompanyTicker','Year','CIK', 'ACCN','Status','CSV.Length'])
for item in filtered_list:
        CompanyName = item
        Companycik = FindCompanyCik(CompanyName)
        Download10kdata(Companycik,CompanyName,downloadRec)
        
# print(downloadRec)

{'cik_str': 1699136, 'ticker': 'WHD', 'title': 'Cactus, Inc.'}
WHD-0001558370-19-002063


Item   start     end
0                  Item 6.    Selected Financial Data  122560  122595
1    Item 1. Business--Organization Structure" above.  127138  127189
2   Item 7.    Management's Discussion and Analysi...  127812  127887
3   Item 1. Business" for information on our produ...  129269  129340
4   Item 8.    Financial Statements and Supplement...  185151  185206
5   Item 9.        Changes in and Disagreements wi...  303768  303847
6   Item 10.    Directors, Executive Officers and ...  310590  310657
7   Item 13. Certain Relationships and Related Par...  325068  325145
8                  Item 11.    Executive Compensation  339685  339720
9   Item 12.    Security Ownership of Certain Bene...  370068  370147
10  Item 13.    Certain Relationships and Related ...  381693  381766
11  Item 11.\nExecutive Compensation--Employment, ...  414834  414921
12  Item 10. Directors, Executive Officers and Cor...  415654  415724
13  Item 14.    Principal Accounting Fees and Serv...  415834  415885
14  Item 15.    Exhibits, Financial Statement Sche...  417173  417225
15                      Item 16.    Form 10‑K Summary  426142  426172

WHD-0001558370-20-001806


Item   start     end
0   Item 7.    Management's Discussion and Analysi...  124985  125060
1   Item 7.\nManagement's Discussion and Analysis ...  126626  126708
2   Item 1. Business" for information on our produ...  127098  127169
3   Item 8.    Financial Statements and Supplement...  158817  158872
4   Item 9.        Changes in and Disagreements wi...  266757  266836
5   Item 10.    Directors, Executive Officers and ...  270045  270112
6   Item 13. Certain Relationships and Related Tra...  286052  286122
7                  Item 11.    Executive Compensation  300141  300176
8   Item 12.    Security Ownership of Certain Bene...  370044  370123
9   Item 13.    Certain Relationships and Related ...  382887  382960
10                                 Item 11. Executive  415768  415787
11  Item 10. Directors, Executive Officers and Cor...  415910  415981
12  Item 14.    Principal Accounting Fees and Serv...  416058  416109
13  Item 15.    Exhibits, Financial Statement Sche...  417728  417780
14  Item 10.17 of the Registrant's Annual Report o...  426740  426978
15                      Item 16.    Form 10‑K Summary  429223  429253

WHD-0001699136-21-000033


...

Item   start     end
0   ITEM 15.|  | Exhibits and Financial Statement ...   31790   31855
1               ITEM 16.|  | Form 10-K Summary|  | 82   31866   31906
2                                    ITEM 1. BUSINESS   31972   31989
3                                  ITEM 2. PROPERTIES  120515  120534
4                           ITEM 3. LEGAL PROCEEDINGS  121455  121481
5                     ITEM 4. MINE SAFETY DISCLOSURES  125291  125323
6                                    ITEM 6. RESERVED  136717  136734
7   ITEM 8. FINANCIAL STATEMENTS AND SUPPLEMENTARY...  201289  201341
8   ITEM 10. DIRECTORS, EXECUTIVE OFFICERS AND COR...  327801  327865
9                                           Item 5.05  328855  328865
10                    ITEM 11. EXECUTIVE COMPENSATION  329187  329219
11  ITEM 12. SECURITY OWNERSHIP OF CERTAIN BENEFIC...  329589  329665
12  ITEM 13. CERTAIN RELATIONSHIPS AND RELATED TRA...  331310  331380
13    ITEM 14. PRINCIPAL ACCOUNTING FEES AND SERVICES  331783  331831
14  ITEM 15. EXHIBITS AND FINANCIAL STATEMENT SCHE...  332378  332430
15                         ITEM 16. FORM 10-K SUMMARY  345631  345658

NVT-0001720635-23-000009


Item   start     end
0   ITEM 15.|  | Exhibits and Financial Statement ...   34480   34545
1               ITEM 16.|  | Form 10-K Summary|  | 84   34556   34596
2                                    ITEM 1. BUSINESS   34662   34679
3                                  ITEM 2. PROPERTIES  120815  120834
4                           ITEM 3. LEGAL PROCEEDINGS  121755  121781
5                     ITEM 4. MINE SAFETY DISCLOSURES  125591  125623
6                                    ITEM 6. RESERVED  137070  137087
7   ITEM 8. FINANCIAL STATEMENTS AND SUPPLEMENTARY...  198618  198670
8   ITEM 10. DIRECTORS, EXECUTIVE OFFICERS AND COR...  332703  332767
9                                           Item 5.05  333757  333767
10                    ITEM 11. EXECUTIVE COMPENSATION  334089  334121
11  ITEM 12. SECURITY OWNERSHIP OF CERTAIN BENEFIC...  334491  334567
12  ITEM 13. CERTAIN RELATIONSHIPS AND RELATED TRA...  336212  336282
13    ITEM 14. PRINCIPAL ACCOUNTING FEES AND SERVICES  336685  336733
14  ITEM 15. EXHIBITS AND FINANCIAL STATEMENT SCHE...  337280  337332
15                         ITEM 16. FORM 10-K SUMMARY  352079  352106

NVT-0001720635-24-000012


Item   start     end
0   ITEM 15.|  | Exhibits and Financial Statement ...   35554   35619
1               ITEM 16.|  | Form 10-K Summary|  | 83   35630   35670
2                                    ITEM 1. BUSINESS   35728   35745
3                                  ITEM 2. PROPERTIES  128048  128067
4                           ITEM 3. LEGAL PROCEEDINGS  128978  129004
5                     ITEM 4. MINE SAFETY DISCLOSURES  132791  132823
6                                    ITEM 6. RESERVED  144744  144761
7   ITEM 8. FINANCIAL STATEMENTS AND SUPPLEMENTARY...  207184  207236
8   ITEM 10. DIRECTORS, EXECUTIVE OFFICERS AND COR...  350811  350875
9                                           Item 5.05  351865  351875
10                    ITEM 11. EXECUTIVE COMPENSATION  352197  352229
11  ITEM 12. SECURITY OWNERSHIP OF CERTAIN BENEFIC...  352599  352675
12  ITEM 13. CERTAIN RELATIONSHIPS AND RELATED TRA...  354318  354388
13    ITEM 14. PRINCIPAL ACCOUNTING FEES AND SERVICES  354814  354862
14  ITEM 15. EXHIBITS AND FINANCIAL STATEMENT SCHE...  355409  355461
15                         ITEM 16. FORM 10-K SUMMARY  371408  371435

In [16]:
display(downloadRec)

CompanyTicker    Year      CIK                  ACCN Status  CSV.Length
0              WHD  2018.0  1699136  0001558370-19-002063   True         284
1              WHD  2019.0  1699136  0001558370-20-001806   True         341
2              WHD  2020.0  1699136  0001699136-21-000033   True         198
3              WHD  2021.0  1699136  0001699136-22-000011   True         207
4              WHD  2022.0  1699136  0001699136-23-000017   True         197
...            ...     ...      ...                   ...    ...         ...
1985           NVT  2019.0  1720635  0001720635-20-000009   True         297
1986           NVT  2020.0  1720635  0001720635-21-000013   True         324
1987           NVT  2021.0  1720635  0001720635-22-000009   True         759
1988           NVT  2022.0  1720635  0001720635-23-000009   True         762
1989           NVT  2023.0  1720635  0001720635-24-000012   True         806

[1990 rows x 6 columns]